- create conda env from file. 
- download PSP data into separate repository. 
- try loading structures in with cif.gz
- proteome class for iterating over list of sites and a given structure directory (i.e. filter out sites with no structure)
- motif class for dealing with phosphosite

In [1]:
# Try and construct graphs per site from structure dir (cif.gz files)

# Try and use structuremap to do the same. 

In [2]:
# Autoreload 
%load_ext autoreload
%autoreload 2

from pathlib import Path 
import pandas as pd 
import numpy as np

# Import structuremap functions
import structuremap.utils
structuremap.utils.set_logger()
from structuremap.processing import download_alphafold_cif, download_alphafold_pae, format_alphafold_data, annotate_accessibility, get_smooth_score, annotate_proteins_with_idr_pattern, get_extended_flexible_pattern, get_proximity_pvals, perform_enrichment_analysis, perform_enrichment_analysis_per_protein, evaluate_ptm_colocalization, extract_motifs_in_proteome
from structuremap.plotting import plot_enrichment, plot_ptm_colocalization

import os 
import re 
import gzip 
import shutil
import Bio.PDB.MMCIF2Dict
from typing import Union, List, Tuple, Dict, Optional
from pathlib import Path

### Load phosphosite dataset

In [163]:
from phosphosite.dataset import phosphorylation # Filtered out isoforms
df = phosphorylation[phosphorylation["ORGANISM"] == "human"]
print(len(df[df["ACC_ID"].str.contains("-")]) / len(df) * 100 )
len(df)

0.0


232587

In [164]:
# Sort by ACC_ID
df = df.sort_values("ACC_ID")

# Filter by residue type, first character in MOD_RSD
allowed_residues = "STY"
df = df[df["MOD_RSD"].str[0].isin(list(allowed_residues))]
df

GENE       PROTEIN        ACC_ID HU_CHR_LOC MOD_RSD  SITE_GRP_ID  \
42799   C19orf48      C19orf48    A0A024R4G9   19q13.33   S20-p     23088226   
42798   C19orf48      C19orf48    A0A024R4G9   19q13.33   S16-p     23088224   
42797   C19orf48      C19orf48    A0A024R4G9   19q13.33   T14-p     23088228   
249210   PPIAL4E       PPIAL4E    A0A075B759     1q21.1   Y79-p     50687016   
249212   PPIAL4E       PPIAL4E    A0A075B759     1q21.1  T119-p     50729117   
...          ...           ...           ...        ...     ...          ...   
69495    COLEC10       COLEC10        Q9Y6Z7    8q24.12  T155-p     15418691   
69494    COLEC10       COLEC10        Q9Y6Z7    8q24.12  S141-p     25287884   
102808   ERVK-19       ERVK-19        Q9YNA8      19q11  S465-p     31094301   
236227     PHF10    PHF10 iso5        S5FZ81       6q27  S376-p     25170312   
18421    ANKRD66  ANKRD66 iso2  XP_016865637     6p12.3    T4-p     34363980   

       ORGANISM  MW_kD         DOMAIN     SITE_+/-7_AA  LT_LIT  MS_LIT  \
42799     human  13.09        DUF5535  ItGsRLLsMVPGPAR     1.0     NaN   
42798     human  13.09        DUF5535  EIQAItGsRLLsMVP     NaN     NaN   
42797     human  13.09        DUF5535  VLEIQAItGsRLLsM     NaN     NaN   
249210    human  18.20  Pro_isomerase  GTGDKSIyGEKFDDE     NaN     NaN   
249212    human  18.20  Pro_isomerase  FFICAAKtEWLDGkH     NaN     NaN   
...         ...    ...            ...              ...     ...     ...   
69495     human  30.71            NaN  VIAGIREtEEKFYYI     NaN     NaN   
69494     human  30.71            NaN  SIARLKTsMKFVKNV     NaN     NaN   
102808    human  74.18      Gag_p24_C  LQDVAQKsIAIEKAR     NaN     1.0   
236227    human  42.61            NaN  GYKVEEKsP______     NaN     5.0   
18421     human  20.16            NaN  ____MVRtACQHRAP     NaN     NaN   

        MS_CST CST_CAT#  Ambiguous_Site  
42799      1.0      NaN               0  
42798      1.0      NaN               0  
42797      1.0      NaN               0  
249210     2.0      NaN               1  
249212     1.0      NaN               1  
...        ...      ...             ...  
69495      1.0      NaN               0  
69494      1.0      NaN               0  
102808     NaN      NaN               0  
236227     NaN      NaN               0  
18421      1.0      NaN               0  

[232557 rows x 15 columns]

### Load structure data

#### Define paths to structural data.

In [5]:
uniprot_id = "P51786"

af_version = 3
filename_template = "AF-{uniprot_id}-F1-model_v{af_version}.cif.gz"
filename = filename_template.format(uniprot_id=uniprot_id, af_version=af_version)

structure_dir = Path.home() / "STRUCTURAL_MOTIFS/DATA/"
af_cif_dir = structure_dir / "AF_HUMAN_CIF" 
af_pdb_dir = structure_dir / "AF_HUMAN_PDB"

# Assert that the cif and pdb directories exist.
assert af_cif_dir.exists()
assert af_pdb_dir.exists()

#### Initialise structure loader object.

In [6]:
from phosphosite.structure import StructureLoader
cif_loader = StructureLoader(af_cif_dir, extension="cif.gz")
filepath = cif_loader.get_structure("Q8WUY3")
filepath

PosixPath('/home/cim/STRUCTURAL_MOTIFS/DATA/AF_HUMAN_CIF/AF-Q8WUY3-F1-model_v3.cif.gz')

In [7]:
pdb_loader = StructureLoader(af_pdb_dir, extension="pdb")
filepath = pdb_loader.get_structure("Q8WUY3")
filepath

PosixPath('/home/cim/STRUCTURAL_MOTIFS/DATA/AF_HUMAN_PDB/AF-Q8WUY3-F1-model_v3.pdb')

In [8]:
protein_ids = list(df["ACC_ID"].unique())
len(protein_ids)

17581

In [9]:
existing_ids = cif_loader.get_existing_ids(protein_ids)
len(existing_ids)

17338

In [10]:
for protein_id in existing_ids:
    # Check that equivalent PDB file exists.
    if not pdb_loader.protein_id_exists(protein_id):
        print(f"Missing PDB file for {protein_id}")

In [11]:
# only use existing 
df = df[df["ACC_ID"].isin(existing_ids)]

## Annotate AlphaFold structures 

In [12]:
# Trim down uniprot ids for now. 
uniprot_ids = existing_ids[0:100]

In [13]:
from phosphosite.structure.processing import process_af_data
structure_df = process_af_data(
    af_cif_dir, 
    out_format="AF-{uniprot_id}-F1-model_v3.cif.gz",
    #protein_ids=existing_ids, 
    protein_ids=uniprot_ids,
)
structure_df[0:2]

100%|██████████| 100/100 [00:24<00:00,  4.06it/s]


protein_id  protein_number AA  position  quality  x_coord_c  x_coord_ca  \
0  A0A075B759               1  M         1    66.72    -19.205     -19.235   
1  A0A075B759               1  V         2    83.11    -17.532     -18.934   

   x_coord_cb  x_coord_n  y_coord_c  ...  z_coord_ca  z_coord_cb  z_coord_n  \
0     -17.818    -20.083      6.188  ...       6.506       7.091      7.169   
1     -19.228    -19.068      6.568  ...       2.733       2.005      4.191   

   secondary_structure  structure_group  BEND  HELX STRN TURN  unstructured  
0         unstructured     unstructured     0     0    0    0             1  
1         unstructured     unstructured     0     0    0    0             1  

[2 rows x 24 columns]

In [14]:
structure_df

protein_id  protein_number AA  position  quality  x_coord_c  \
0      A0A075B759               1  M         1    66.72    -19.205   
1      A0A075B759               1  V         2    83.11    -17.532   
2      A0A075B759               1  N         3    88.43    -15.452   
3      A0A075B759               1  S         4    93.22    -12.711   
4      A0A075B759               1  V         5    97.80    -10.210   
...           ...             ... ..       ...      ...        ...   
65999      A4D126             100  Q       447    98.10    -25.830   
66000      A4D126             100  L       448    96.78    -25.579   
66001      A4D126             100  L       449    97.54    -24.192   
66002      A4D126             100  I       450    96.53    -22.755   
66003      A4D126             100  A       451    95.08    -22.308   

       x_coord_ca  x_coord_cb  x_coord_n  y_coord_c  ...  z_coord_ca  \
0         -19.235     -17.818    -20.083      6.188  ...       6.506   
1         -18.934     -19.228    -19.068      6.568  ...       2.733   
2         -16.160     -16.404    -17.439      6.076  ...       1.051   
3         -13.566     -12.681    -14.405      6.888  ...      -0.110   
4         -11.417     -11.992    -12.403      8.060  ...      -3.217   
...           ...         ...        ...        ...  ...         ...   
65999     -25.390     -23.946    -25.528     -8.684  ...      15.235   
66000     -26.684     -28.069    -26.439     -8.257  ...      18.368   
66001     -23.644     -22.400    -24.681     -6.427  ...      20.492   
66002     -23.977     -24.619    -23.561     -5.226  ...      24.107   
66003     -21.936     -21.731    -22.931     -3.053  ...      25.859   

       z_coord_cb  z_coord_n  secondary_structure  structure_group  BEND  \
0           7.091      7.169         unstructured     unstructured     0   
1           2.005      4.191         unstructured     unstructured     0   
2           0.356      1.501         unstructured     unstructured     0   
3           0.812      0.661         unstructured     unstructured     0   
4          -4.645     -2.232                 STRN             STRN     0   
...           ...        ...                  ...              ...   ...   
65999      15.547     13.819         unstructured     unstructured     0   
66000      18.994     17.268                 STRN             STRN     0   
66001      19.880     19.472                 STRN             STRN     0   
66002      25.092     22.863                 STRN             STRN     0   
66003      25.184     25.123         unstructured     unstructured     0   

       HELX STRN TURN  unstructured  
0         0    0    0             1  
1         0    0    0             1  
2         0    0    0             1  
3         0    0    0             1  
4         0    1    0             0  
...     ...  ...  ...           ...  
65999     0    0    0             1  
66000     0    1    0             0  
66001     0    1    0             0  
66002     0    1    0             0  
66003     0    0    0             1  

[66004 rows x 24 columns]

#### Graphein subgraph method.

In [15]:
pd.options.mode.chained_assignment = None  # default='warn'

In [22]:
from graphein.protein.config import ProteinGraphConfig
config = ProteinGraphConfig()

from graphein.protein.graphs import construct_graph
from graphein.protein.visualisation import plotly_protein_structure_graph



In [27]:
uniprot_id = "Q8WUY3"

In [29]:
pdb_path = pdb_loader.get_structure(uniprot_id)
g = construct_graph(config=config, path=pdb_path)

Output()

/home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py:160: FutureWarning:

The default value of regex will change from True to False in a future version.

/home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py:163: FutureWarning:

The default value of regex will change from True to False in a future version.

[06/05/23 16:58:19] DEBUG    Deprotonating protein. This removes H atoms from the pdb_df dataframe    ]8;id=902164;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py\graphs.py]8;;\:]8;id=994566;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py#186\186]8;;\

                    DEBUG    Detected 1400 total nodes                                                ]8;id=216644;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py\graphs.py]8;;\:]8;id=490998;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py#438\438]8;;\

In [31]:
# Get sites for this uniprot_id 

site_df = df[df["ACC_ID"] == uniprot_id]
len(site_df)


49

In [32]:
sites = list(site_df["MOD_RSD"].unique())
len(sites)

49

In [25]:
p = plotly_protein_structure_graph(
    g,
    colour_edges_by="kind",
    colour_nodes_by="degree",
    label_node_ids=False,
    plot_title="Peptide backbone graph. Nodes coloured by degree.",
    node_size_multiplier=1
    )
p.show()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

In [66]:
from phosphosite.graphs import get_motif_subgraph
from phosphosite.utils import aa1to3

chain_id = "A"
g.graph[f"sequence_{chain_id}"]

'MEEFLQRAKSKLNRSKRLEKVHVVIGPKSCDLDSLISTFTYAYFLDKVSPPGVLCLPVLNIPRTEFNYFTETRFILEELNISESFHIFRDEINLHQLNDEGKLSITLVGSSVLASEDKTLESAVVKVINPVEQSDANVEFRESSSSLVLKEILQEAPELITEQLAHRLRGSILFKWMTMESEKISEKQEEILSILEEKFPNLPPREDIINVLQETQFSAQGLSIEQTMLKDLKELSDGEIKVAISTVSMNLENCLFHSNITSDLKAFTDKFGFDVLILFSSYLSEEQQPRRQIAVYSENMELCSQICCELEECQNPCLELEPFDCGCDEILVYQQEDPSVTCDQVVLVVKEVINRRCPEMVSNSRTSSTEAVAGSAPLSQGSSGIMELYGSDIEPQPSSVNFIENPPDLNDSNQAQVDANVDLVSPDSGLATIRSSRSSKESSVFLSDDSPVGEGAGPHHTLLPGLDSYSPIPEGAVAEEHAWSGEHGEHFDLFNFDPAPMASGQSQQSSHSADYSPADDFFPNSDLSEGQLPAGPEGLDGMGTNMSNYSSSSLLSGAGKDSLVEHDEEFVQRQDSPRDNSERNLSLTDFVGDESPSPERLKNTGKRIPPTPMNSLVESSPSTEEPASLYTEDMTQKATDTGHMGPPQTHARCSSWWGGLEIDSKNIADAWSSSEQESVFQSPESWKEHKPSSIDRRASDSVFQPKSLEFTKSGPWESEFGQPELGSNDIQDKNEESLPFQNLPMEKSPLPNTSPQGTNHLIEDFASLWHSGRSPTAMPEPWGNPTDDGEPAAVAPFPAWSAFGKEDHDEALKNTWNLHPTSSKTPSVRDPNEWAMAKSGFAFSSSELLDNSPSEINNEAAPEIWGKKNNDSRDHIFAPGNPSSDLDHTWTNSKPPKEDQNGLVDPKTRGKVYEKVDSWNLFEENMKKGGSDVLVPWEDSFLSYKCSDYSASNLGEDSVPSPLDTNYSTSDSYTSPTFAGDEKETEHKPFAKEEGFESK

In [123]:
s_g.nodes

NodeView(('A:GLY:80', 'A:TYR:79', 'A:ILE:78', 'A:SER:77'))

In [115]:
node_id

'A:TYR:79'

In [116]:
s_g[node_id]

AtlasView({'A:GLY:80': {'kind': {'peptide_bond'}, 'distance': 3.8600312174903455}, 'A:ILE:78': {'kind': {'peptide_bond'}, 'distance': 3.8591601417925117}})

In [109]:
type(s_g[node_id])

networkx.classes.coreviews.AtlasView

In [107]:
list(s_g[node_id])

['A:GLY:80', 'A:ILE:78']

In [128]:
site_coords = s_g.nodes[node_id]["coords"]
type(site_coords)



numpy.ndarray

In [129]:
from phosphosite.structure.processing import get_3d_dist

In [147]:
candidate_nodes = [
            s_g.nodes[i]
            for i in s_g.nodes
            if i not in [prev_node_id]
        ]

type(candidate_nodes[0])

dict

In [133]:
for i in s_g.nodes(data=True):
    s_g.nodes

In [134]:
site_coords = s_g.nodes[node_id]["coords"]

array([-3.653,  8.871, 15.889])

In [144]:
def get_euc_dist(
    arr1: np.ndarray, arr2: np.ndarray
): 
    """Get euclidean distance between two arrays."""
    return np.sqrt(np.sum((arr1 - arr2) ** 2))
    

In [148]:
[
    get_euc_dist(site_coords, node["coords"])
    for node in candidate_nodes
]


[3.8600312174903455, 0.0, 5.231354509111383]

In [152]:
node_dict = candidate_nodes[0]
node_dict

{'chain_id': 'A',
 'residue_name': 'GLY',
 'residue_number': 80,
 'atom_type': 'CA',
 'element_symbol': 'C',
 'coords': array([-1.3000e-02,  8.7510e+00,  1.7168e+01]),
 'b_factor': 95.24,
 'meiler': dim_1    0.00
 dim_2    0.00
 dim_3    0.00
 dim_4    0.00
 dim_5    6.07
 dim_6    0.13
 dim_7    0.15
 Name: GLY, dtype: float64}

['A', 'GLY', 80]

'A:GLY:80'

In [199]:
def get_node_id(
    site: str, 
    chain_id: str = "A",
) -> str: 
    mod_rsd, modification = site.split("-")
    aa = aa1to3[mod_rsd[0]]
    position = mod_rsd[1:]
    node_id = f"{chain_id}:{aa}:{position}"
    return node_id

def generate_node_id(
    node_dict: Dict[str, Union[str, int]],
    delimiter: str = ":",
) -> str: 
    return delimiter.join([str(node_dict[s]) for s in ["chain_id", "residue_name", "residue_number"]])

In [200]:
failed = []
sequence_dict = {}

radius = 6.0
chain_id = "A"
force = False

out_dir = Path(f"data/processed/motifs")
out_file_format = "{uniprot_id}-R{radius}Å.csv", 



skip_empty_motifs = False # if False, still write NaN to file.

for uniprot_id in uniprot_ids:

    # Check that .csv file exists for this uniprot_id.
    if not force:
        out_file = out_dir / out_file_format.format(
            uniprot_id=uniprot_id, 
            radius=radius,
        )
        if out_file.exists():
            print(f"Skipping {uniprot_id}. File exists.")
            continue

    # Construct graph. 
    pdb_path = pdb_loader.get_structure(uniprot_id)
    g = construct_graph(config=config, path=pdb_path)

    sequence_dict[uniprot_id] = g.graph[f"sequence_{chain_id}"]

    # Get sites for this uniprot_id
    site_df = df[df["ACC_ID"] == uniprot_id]
    sites = list(site_df["MOD_RSD"].unique())

    dict_list = []
    for site in sites:
        node_id = get_node_id(site)
        if node_id in g.nodes:
            s_g = get_motif_subgraph(
                g, 
                node_id, 
                radius = radius, # 5.0
            )
        else: 
            print(f"Node {node_id} not in graph ({uniprot_id}).")
            failed.append((uniprot_id, node_id))
            continue

        # Get nearest node to site.
        
        # Extract out adjacent residues (prev and next in sequence) 
        pos = int(node_id.split(":")[2])
        next_pos = pos + 1
        prev_pos = pos - 1
        seq = g.graph[f'sequence_{chain_id}']
        # sequence is 0 indexed 
        
        # Check if out of range. 
        if next_pos > len(seq):
            next_node_id = np.nan
        else:   
            next_node_id = f"{chain_id}:{aa1to3[seq[next_pos - 1]]}:{next_pos}"
        
        if prev_pos < 1:
            prev_node_id = np.nan
        else:
            prev_node_id = f"{chain_id}:{aa1to3[seq[prev_pos - 1]]}:{prev_pos}"

        site_coords = s_g.nodes[node_id]["coords"]

        candidate_nodes = [
            s_g.nodes[i]
            for i in s_g.nodes
            if i not in [prev_node_id, node_id, next_node_id] # Not the modified residue, or sequence adjacent residues.
        ]
        if len(candidate_nodes) == 0:
            print(f"No candidate nodes for {uniprot_id} {node_id}.")
            nearest_node = np.nan

            if skip_empty_motifs: 
                continue # don't create data for this motif.
        else:
            # Pick node with smallest euclidean distance to site.
            nearest_node = min(
                candidate_nodes,
                key=lambda node: get_euc_dist(site_coords, node["coords"]),
            )
            nearest_node = generate_node_id(nearest_node)
    
        dict_list.append(dict(
            uniprot_id=uniprot_id,
            prev=prev_node_id,
            site=node_id,
            next=next_node_id,
            nearest_node=nearest_node, # nearest that's prev or next. NaN if none. 
        ))
    
    
    motif_df = pd.DataFrame.from_dict(dict_list)
    motif_df.to_csv(
        out_dir / out_file_format.format(uniprot_id, radius),
        index=False,
        # Tab delimited for easy reading.
        sep="\t",
        # Include column names.
        header=True,
    )

Output()

/home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py:160: FutureWarning:

The default value of regex will change from True to False in a future version.

/home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py:163: FutureWarning:

The default value of regex will change from True to False in a future version.

[06/05/23 19:02:06] DEBUG    Deprotonating protein. This removes H atoms from the pdb_df dataframe    ]8;id=205931;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py\graphs.py]8;;\:]8;id=947874;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py#186\186]8;;\

                    DEBUG    Detected 164 total nodes                                                 ]8;id=924735;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py\graphs.py]8;;\:]8;id=272385;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/graphs.py#438\438]8;;\

...

                    DEBUG    Creating subgraph from nodes: ['A:THR:265', 'A:ASP:269', 'A:TYR:266',  ]8;id=75310;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py\subgraphs.py]8;;\:]8;id=118898;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py#57\57]8;;\
                             'A:MET:60', 'A:ARG:268', 'A:LYS:267'].                                                

                    DEBUG    Found 5 nodes in the spatial point-radius subgraph.                   ]8;id=609686;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py\subgraphs.py]8;;\:]8;id=450184;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py#120\120]8;;\

                    DEBUG    Creating subgraph from nodes: ['A:LEU:261', 'A:GLY:257', 'A:SER:258',  ]8;id=576384;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py\subgraphs.py]8;;\:]8;id=622072;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py#57\57]8;;\
                             'A:PRO:259', 'A:ASP:260'].                                                            

                    DEBUG    Found 7 nodes in the spatial point-radius subgraph.                   ]8;id=811260;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py\subgraphs.py]8;;\:]8;id=682402;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py#120\120]8;;\

                    DEBUG    Creating subgraph from nodes: ['A:ILE:109', 'A:TYR:112', 'A:ILE:108',  ]8;id=138414;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py\subgraphs.py]8;;\:]8;id=550152;file:///home/cim/anaconda3/envs/phosphosite/lib/python3.9/site-packages/graphein/protein/subgraphs.py#57\57]8;;\
                             'A:GLN:110', 'A:GLN:113', 'A:HIS:114', 'A:LYS:111'].                                  

In [198]:
len(seq)

921

In [173]:
failed

[('A0A087WUL8', 'A:SER:2804'),
 ('A0A087WUL8', 'A:SER:3048'),
 ('A0A087WUL8', 'A:SER:2316'),
 ('A0A087WUL8', 'A:SER:2560'),
 ('A0A087WUL8', 'A:SER:3536'),
 ('A0A087WUL8', 'A:SER:2072'),
 ('A0A087WUL8', 'A:SER:1828'),
 ('A0A087WUL8', 'A:SER:1584'),
 ('A0A087WUL8', 'A:SER:3292')]

In [176]:
for f in Path("data/processed/motifs").glob("*.csv"):
    f

In [190]:
radius

5.0

In [193]:
# Load dataframes 

# For each file that ends with .csv, load it into a dataframe.
motif_dfs = [
    pd.read_csv(
        f, 
        header=0,
        delimiter="\t",
    )
    for f in Path("data/processed/motifs").glob(f"*-R{radius}Å.csv")
]
motif_df = pd.concat(motif_dfs)
motif_df

uniprot_id        prev        site        next nearest_node
0  A0A096LP55    A:LEU:10    A:THR:11    A:GLU:12          NaN
0  A0A096LP49   A:PRO:565   A:SER:566   A:PRO:567          NaN
1  A0A096LP49   A:GLY:518   A:SER:519   A:PRO:520          NaN
2  A0A096LP49   A:GLU:477   A:SER:478   A:PRO:479          NaN
0  A0A0B4J2A2   A:LYS:118   A:THR:119   A:GLU:120          NaN
1  A0A0B4J2A2   A:GLY:109   A:SER:110   A:GLN:111          NaN
2  A0A0B4J2A2    A:LEU:98    A:SER:99   A:MET:100    A:ALA:128
3  A0A0B4J2A2    A:GLY:94    A:SER:95    A:GLY:96    A:THR:116
4  A0A0B4J2A2    A:ILE:78    A:TYR:79    A:GLY:80          NaN
5  A0A0B4J2A2    A:LEU:39    A:SER:40    A:THR:41    A:GLY:162
0  A0A075B759    A:ILE:78    A:TYR:79    A:GLY:80          NaN
1  A0A075B759   A:LYS:118   A:THR:119   A:GLU:120          NaN
2  A0A075B759    A:HIS:92    A:THR:93    A:GLY:94          NaN
3  A0A075B759    A:LEU:39    A:SER:40    A:THR:41    A:GLY:162
0  A0A087WUL8  A:ASP:1339  A:SER:1340  A:LEU:1341          NaN
1  A0A087WUL8  A:ASP:1095  A:SER:1096  A:LEU:1097          NaN
2  A0A087WUL8   A:ASP:851   A:SER:852   A:LEU:853          NaN
3  A0A087WUL8   A:ASP:607   A:SER:608   A:LEU:609          NaN
4  A0A087WUL8   A:ASP:363   A:SER:364   A:LEU:365          NaN

In [188]:
nearest_node = motif_df[~motif_df["nearest_node"].isna()]
nearest_node

uniprot_id      prev      site       next nearest_node
2  A0A0B4J2A2  A:LEU:98  A:SER:99  A:MET:100    A:ALA:128
3  A0A0B4J2A2  A:GLY:94  A:SER:95   A:GLY:96    A:THR:116
5  A0A0B4J2A2  A:LEU:39  A:SER:40   A:THR:41    A:GLY:162
3  A0A075B759  A:LEU:39  A:SER:40   A:THR:41    A:GLY:162

In [187]:
nearest_node["uniprot_id"].unique()

array(['A0A0B4J2A2', 'A0A075B759'], dtype=object)